In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
signal = pd.read_excel("secom.xlsx")
label = pd.read_excel("secom_labels.xlsx")
secom = pd.concat([signal, label], axis = 1)
secom = secom.drop('date', axis=1)

pd.set_option('display.max_columns',None)
pd.set_option('display.max_rows',None)
secom_std_0 = []
for name, std in zip(signal, secom.describe().loc['std']):
    if std == 0:
        secom_std_0.append(name)
secom = secom.drop(secom_std_0,axis=1)
secom_missing = (secom.isnull().sum() / len(secom)).sort_values(ascending = False)

secom_missing_remove = secom_missing.index[secom_missing > 0.63]
secom = secom.drop(secom_missing_remove ,axis = 1)

from sklearn.impute import KNNImputer
imputer = KNNImputer(n_neighbors = 3)
secom_impute = imputer.fit_transform(secom)
secom_impute = pd.DataFrame(secom_impute)
secom_impute.columns = list(secom)
X = secom_impute.drop('test', axis=1)
y = secom['test']

In [2]:
from sklearn.ensemble import RandomForestClassifier
rnd_clf = RandomForestClassifier(random_state=42,class_weight='balanced')
rnd_clf.fit(X,y)
secom_feature_names = list(secom_impute)
rnd_forest_feature_importance = []
for name, score in zip(secom_feature_names, rnd_clf.feature_importances_):
    rnd_forest_feature_importance.append([name,score])
d = sorted(rnd_forest_feature_importance, key=lambda x : -x[1])
d_=pd.DataFrame(d)
d_['cumulative_importance']=np.cumsum(d_[1])
d_.columns = ['signal','rf_importance','cumulative_importance']
d_

signal  rf_importance  cumulative_importance
0     signal60   2.128748e-02               0.021287
1     signal34   1.158753e-02               0.032875
2    signal520   1.098705e-02               0.043862
3    signal131   1.065821e-02               0.054520
4    signal104   1.060899e-02               0.065129
5    signal248   1.038502e-02               0.075514
6     signal65   9.284544e-03               0.084799
7     signal59   8.078362e-03               0.092877
8     signal22   6.676086e-03               0.099553
9    signal349   6.293850e-03               0.105847
10   signal478   6.268851e-03               0.112116
11   signal153   6.126036e-03               0.118242
12    signal32   6.034816e-03               0.124277
13   signal127   5.988201e-03               0.130265
14    signal29   5.636025e-03               0.135901
15   signal130   5.379972e-03               0.141281
16   signal564   5.347005e-03               0.146628
17    signal20   5.313319e-03               0.151941
18    signal66   5.285803e-03               0.157227
19   signal461   5.217217e-03               0.162444
20   signal337   5.175286e-03               0.167620
21   signal211   5.084794e-03               0.172704
22   signal291   5.061994e-03               0.177766
23   signal201   5.045749e-03               0.182812
24   signal511   4.921131e-03               0.187733
25   signal342   4.880841e-03               0.192614
26   signal299   4.780757e-03               0.197395
27   signal122   4.657476e-03               0.202052
28    signal36   4.650996e-03               0.206703
29   signal386   4.644510e-03               0.211348
30    signal92   4.498189e-03               0.215846
31   signal469   4.429783e-03               0.220276
32   signal344   4.393800e-03               0.224670
33   signal320   4.389494e-03               0.229059
34    signal17   4.376051e-03               0.233435
35   signal113   4.321023e-03               0.237756
36   signal125   4.309328e-03               0.242066
37   signal184   4.174198e-03               0.246240
38    signal62   4.163175e-03               0.250403
39   signal156   4.157244e-03               0.254560
40   signal116   4.046775e-03               0.258607
41    signal82   3.984351e-03               0.262591
42   signal453   3.971796e-03               0.266563
43   signal572   3.971471e-03               0.270535
44   signal289   3.968738e-03               0.274503
45   signal418   3.967589e-03               0.278471
46   signal103   3.960232e-03               0.282431
47    signal77   3.950534e-03               0.286382
48    signal26   3.950460e-03               0.290332
49   signal540   3.930749e-03               0.294263
50   signal426   3.871786e-03               0.298135
51     signal9   3.705096e-03               0.301840
52   signal123   3.639594e-03               0.305479
53    signal76   3.623100e-03               0.309102
54   signal183   3.533522e-03               0.312636
55   signal308   3.504048e-03               0.316140
56    signal56   3.500424e-03               0.319640
57   signal169   3.475607e-03               0.323116
58   signal541   3.474095e-03               0.326590
59    signal80   3.431260e-03               0.330021
60    signal18   3.416561e-03               0.333438
61   signal132   3.353551e-03               0.336792
62   signal576   3.296566e-03               0.340088
63    signal41   3.263099e-03               0.343351
64   signal470   3.262954e-03               0.346614
65    signal69   3.258826e-03               0.349873
66   signal409   3.253234e-03               0.353126
67   signal181   3.249286e-03               0.356375
68     signal1   3.233265e-03               0.359609
69   signal417   3.218963e-03               0.362828
70   signal558   3.178747e-03               0.366006
71    signal16   3.153547e-03               0.369160
72   signal432   3.107028e-03               0.372267
73   signal455   3.105731e-03               0.375373
74   signal106   3.102534e-03    

In [3]:
from sklearn.ensemble import GradientBoostingClassifier
gbm = GradientBoostingClassifier(random_state=42)
gbm.fit(X,y)
secom_feature_names = list(secom_impute)
gbm_feature_importance = []
for name, score in zip(secom_feature_names, gbm.feature_importances_):
    gbm_feature_importance.append([name,score])
d2 = sorted(gbm_feature_importance, key=lambda x : -x[1])
d2_ = pd.DataFrame(d2)
d2_['cumulative_importance']=np.cumsum(d2_[1])
d2_.columns = ['signal', 'gbm_importance', 'cumulative_importance']
d2_

signal  gbm_importance  cumulative_importance
0     signal60    5.704086e-02               0.057041
1     signal65    5.258798e-02               0.109629
2    signal427    3.445340e-02               0.144082
3    signal334    2.584892e-02               0.169931
4    signal442    2.196453e-02               0.191896
5    signal542    1.959965e-02               0.211495
6    signal563    1.909302e-02               0.230588
7      signal3    1.707254e-02               0.247661
8     signal17    1.572813e-02               0.263389
9    signal349    1.562841e-02               0.279017
10   signal581    1.545554e-02               0.294473
11   signal133    1.529156e-02               0.309765
12   signal457    1.518818e-02               0.324953
13    signal41    1.431293e-02               0.339266
14   signal153    1.366781e-02               0.352933
15    signal26    1.341924e-02               0.366353
16   signal575    1.312299e-02               0.379476
17   signal104    1.306285e-02               0.392539
18   signal305    1.287517e-02               0.405414
19   signal122    1.249021e-02               0.417904
20   signal414    1.232351e-02               0.430227
21   signal182    1.203551e-02               0.442263
22   signal268    1.115433e-02               0.453417
23   signal120    1.071649e-02               0.464134
24    signal39    1.007981e-02               0.474214
25   signal540    1.005294e-02               0.484267
26    signal52    9.902103e-03               0.494169
27   signal342    9.222457e-03               0.503391
28   signal100    9.021512e-03               0.512413
29   signal526    9.015039e-03               0.521428
30    signal34    8.804263e-03               0.530232
31   signal461    8.563473e-03               0.538795
32   signal434    8.528332e-03               0.547324
33   signal454    8.236306e-03               0.555560
34   signal211    8.191604e-03               0.563752
35   signal436    7.867742e-03               0.571619
36   signal115    7.672747e-03               0.579292
37    signal72    7.543669e-03               0.586836
38   signal228    7.416860e-03               0.594253
39   signal572    7.321517e-03               0.601574
40   signal131    6.928129e-03               0.608502
41   signal483    6.547641e-03               0.615050
42   signal307    6.474812e-03               0.621525
43   signal311    6.232110e-03               0.627757
44   signal148    6.154062e-03               0.633911
45   signal489    6.153141e-03               0.640064
46    signal30    6.077799e-03               0.646142
47   signal121    5.878793e-03               0.652021
48    signal27    5.871699e-03               0.657892
49   signal431    5.826209e-03               0.663719
50    signal89    5.809495e-03               0.669528
51    signal82    5.739973e-03               0.675268
52   signal589    5.650144e-03               0.680918
53   signal468    5.468500e-03               0.686387
54   signal494    5.456779e-03               0.691843
55   signal249    5.406254e-03               0.697250
56   signal324    5.358126e-03               0.702608
57   signal449    5.192422e-03               0.707800
58    signal23    5.187662e-03               0.712988
59   signal108    5.091897e-03               0.718080
60   signal562    5.016739e-03               0.723097
61   signal357    4.971628e-03               0.728068
62    signal31    4.946901e-03               0.733015
63   signal351    4.927885e-03               0.737943
64   signal105    4.861950e-03               0.742805
65   signal521    4.799376e-03               0.747604
66   signal364    4.771864e-03               0.752376
67   signal580    4.690492e-03               0.757067
68   signal213    4.672856e-03               0.761739
69   signal478    4.496908e-03               0.766236
70   signal438    4.390367e-03               0.770627
71   signal226    4.388157e-03               0.775015
72    signal59    4.359125e-03               0.779374
73   signal4

In [4]:
cor_list = []
for i in X.columns.tolist():
    cor = np.corrcoef(X[i], y)[0, 1]
    cor_list.append([i,cor])
d3 = sorted(cor_list, key=lambda x :- abs(x[1]))
d3_ = pd.DataFrame(d3)
d3_.columns = ['signal','corr']
d3_

signal      corr
0     signal60  0.155532
1    signal104  0.150879
2    signal511  0.131335
3    signal349  0.129725
4    signal432  0.119781
5    signal435  0.111289
6    signal431  0.109450
7     signal29 -0.109217
8    signal436  0.108236
9     signal22  0.106876
10   signal437  0.106167
11   signal130  0.102986
12   signal211  0.102011
13   signal299  0.101603
14   signal164  0.099392
15   signal125  0.094183
16   signal296  0.091172
17   signal317 -0.089365
18   signal161  0.089075
19   signal165  0.087220
20   signal300  0.087215
21   signal122  0.085170
22   signal301  0.084243
23   signal166  0.083724
24   signal126 -0.083574
25   signal295  0.082137
26    signal34  0.080975
27    signal27 -0.080911
28   signal181 -0.078577
29    signal80  0.078248
30   signal160  0.078246
31   signal123 -0.078042
32   signal453 -0.077025
33   signal131  0.076495
34    signal65  0.076132
35   signal128 -0.074803
36    signal23 -0.072650
37   signal124  0.072640
38   signal438  0.070737
39    signal15 -0.069273
40   signal115  0.068655
41   signal134  0.067758
42   signal250  0.066478
43   signal388  0.066315
44   signal101  0.064759
45    signal57  0.063904
46   signal461  0.060572
47    signal96  0.060502
48   signal201  0.060380
49   signal472  0.059546
50    signal64  0.058929
51   signal248  0.058701
52    signal77 -0.056399
53   signal456  0.056168
54   signal478  0.056137
55   signal198  0.056100
56    signal59  0.055518
57   signal184  0.055514
58   signal366  0.055188
59   signal558  0.054947
60   signal469 -0.054912
61   signal512  0.054901
62   signal127  0.054855
63    signal66  0.054797
64   signal552  0.054538
65   signal555  0.053976
66   signal338  0.053666
67   signal206  0.053581
68   signal197  0.053546
69   signal320  0.052913
70   signal470  0.052773
71   signal576 -0.052731
72   signal167  0.052716
73    signal39  0.052682
74    signal41 -0.052379
75    signal69 -0.052108
76    signal33  0.052101
77   signal200  0.052031
78   signal574 -0.051873
79   signal544 -0.051600
80   signal520  0.051475
81   signal543 -0.050912
82    signal91 -0.050489
83   signal563 -0.050426
84   signal281 -0.050332
85    signal71 -0.050197
86   signal342  0.049642
87   signal578 -0.049633
88   signal334  0.048743
89    signal32 -0.048684
90   signal302  0.048076
91   signal424  0.047874
92   signal139  0.047669
93   signal282 -0.047527
94   signal412  0.047475
95   signal189  0.047053
96   signal583  0.046947
97   signal100  0.046893
98   signal546 -0.046248
99   signal434  0.045586
100  signal350  0.045516
101  signal204  0.045414
102  signal551  0.045137
103  signal548  0.044980
104  signal489 -0.044540
105  signal476  0.044371
106  signal212  0.044338
107  signal554  0.044317
108  signal214  0.044285
109   signal79 -0.043951
110  signal146 -0.043763
111  signal116 -0.043654
112  signal103 -0.043447
113  signal352  0.043330
114  signal147 -0.043310
115  signal182 -0.043156
116  signal485 -0.042796
117  signal176  0.042748
118  signal418 -0.042507
119  signal557  0.041936
120  signal570  0.041838
121  signal144 -0.041836
122  signal228  0.041811
123  signal454 -0.041478
124  signal447  0.041410
125   signal38  0.041406
126  signal335  0.041089
127  signal417 -0.040265
128  signal199  0.039934
129  signal480  0.039786
130  signal337  0.039628
131   signal68  0.039584
132  signal325  0.039568
133  signal318 -0.039538
134  signal311  0.039402
135  signal105 -0.039023
136  signal361  0.038608
137  signal471  0.038560
138  signal280 -0.038247
139  signal145 -0.038211
140   signal31  0.037904
141  signal446  0.037722
142   signal67 -0.037636
143  signal175  0.037165
144  signal173  0.037146
145  signal196  0.036808
146  signal444  0.036736
147  signal522  0.036722
148  signal171  0.036391
149   signal26 -0.036270
150  signal468  0.036214
151  signal319 -0.035498
152  signal588  0.035433
153  signal208  0.035404
154  signal495  0.035182
155  signal333  0.034833
156  signal378 -0.034821
157  signal575 -0.034713
158  signal332  0.034654
159  sig

In [5]:
from sklearn.linear_model import Lasso
from sklearn.metrics import roc_auc_score
alphas = [100, 10, 1, 0.1, 0.01, 0.001, 0.0001]
from sklearn.preprocessing import MinMaxScaler
X_norm = MinMaxScaler().fit_transform(X)
auc_lasso = []
for alpha in alphas:
    lasso = Lasso(alpha=alpha)
    lasso.fit(X_norm, y)
    pred = lasso.predict(X)
    auc_lasso.append(roc_auc_score(y,pred))
auc_lasso

C:\Users\mstar\anaconda3\lib\site-packages\sklearn\linear_model\_coordinate_descent.py:530: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 1.7930917413100929, tolerance: 0.03883905552010211
  model = cd_fast.enet_coordinate_descent(


[0.5,
 0.5,
 0.5,
 0.5,
 0.6197158105052842,
 0.6776052894473947,
 0.5531836584468164]

In [6]:
lasso_001 = Lasso(alpha=0.001)
lasso_001.fit(X_norm, y)
lasso_pred_001 = lasso_001.predict(X_norm)
lasso_feature_weight = []
for name, weight in zip(secom_feature_names, lasso_001.coef_):
    lasso_feature_weight.append([name,weight])
d4 = sorted(lasso_feature_weight, key=lambda x :- abs(x[1]))
d4_ = pd.DataFrame(d4)
d4_.columns = ['signal','coef_weights']
d4_

signal  coef_weights
0     signal60      1.121831
1    signal349      0.501068
2     signal65      0.344917
3    signal438      0.322669
4    signal511      0.285707
5     signal76      0.264973
6    signal130      0.246233
7    signal432      0.209047
8    signal563     -0.180147
9     signal34      0.179167
10   signal350      0.164158
11   signal461      0.151567
12   signal115      0.135285
13   signal133     -0.134597
14   signal146     -0.130507
15    signal15     -0.123904
16   signal282     -0.114425
17   signal131      0.112897
18   signal444      0.110333
19   signal481     -0.108459
20   signal144     -0.105298
21   signal564     -0.103807
22   signal156     -0.102406
23   signal313     -0.100202
24    signal22      0.098079
25   signal104      0.097836
26   signal570      0.096669
27   signal353     -0.096600
28   signal489     -0.096007
29   signal542      0.095703
30   signal317     -0.095533
31   signal122      0.093046
32    signal23     -0.092943
33    signal82      0.088172
34    signal32     -0.086115
35   signal101      0.084699
36    signal87      0.081230
37   signal320      0.080661
38   signal100      0.080526
39    signal91     -0.078688
40   signal576     -0.078062
41   signal485     -0.076089
42   signal588      0.074902
43    signal59      0.069740
44   signal512      0.067701
45   signal434      0.066653
46    signal29     -0.060815
47   signal544     -0.058673
48   signal456      0.058385
49    signal77     -0.057461
50   signal312     -0.056887
51    signal33      0.055735
52   signal583      0.053676
53   signal486     -0.053434
54   signal412      0.052067
55   signal549     -0.047299
56   signal116     -0.043403
57   signal522      0.040754
58   signal582     -0.040494
59   signal132      0.039727
60   signal311      0.039320
61   signal217      0.039296
62   signal219     -0.037025
63   signal127      0.036782
64   signal487      0.036042
65    signal41     -0.035968
66   signal103     -0.034245
67   signal501      0.034202
68   signal488      0.029880
69    signal48      0.028431
70    signal57      0.026341
71   signal578     -0.025725
72   signal419     -0.025146
73   signal559      0.022604
74   signal500     -0.022486
75   signal548      0.021906
76   signal490      0.020376
77   signal572     -0.018463
78   signal454     -0.017979
79   signal134      0.016638
80   signal196      0.015027
81   signal562      0.014868
82   signal420      0.014805
83   signal345     -0.011939
84   signal473      0.010671
85    signal89      0.010257
86   signal125      0.009369
87   signal366      0.008433
88   signal425     -0.008228
89   signal162     -0.006999
90    signal61      0.006708
91    signal85     -0.006382
92     signal2     -0.004564
93   signal469     -0.003509
94   signal123     -0.001667
95   signal483     -0.001545
96   signal215     -0.000289
97     signal1     -0.000000
98     signal3     -0.000000
99     signal4     -0.000000
100    signal5     -0.000000
101    signal7      0.000000
102    signal8      0.000000
103    signal9      0.000000
104   signal10     -0.000000
105   signal11      0.000000
106   signal12     -0.000000
107   signal13      0.000000
108   signal16      0.000000
109   signal17      0.000000
110   signal18     -0.000000
111   signal19     -0.000000
112   signal20      0.000000
113   signal21      0.000000
114   signal24      0.000000
115   signal25     -0.000000
116   signal26      0.000000
117   signal27     -0.000000
118   signal28      0.000000
119   signal30     -0.000000
120   signal31     -0.000000
121   signal35     -0.000000
122   signal36     -0.000000
123   signal37      0.000000
124   signal38      0.000000
125   signal39     -0.000000
126   signal40     -0.000000
127   signal42     -0.000000
128   signal44     -0.000000
129   signal45      0.000000
130   signal46      0.000000
131   signal47      0.000000
132   signal49     -0.000000
133   signal51     -0.000000
134   signal52      0.000000
135   signal54     -0.000000
136   signal55     -0.000000
137   

In [7]:
d_TF = (d_['cumulative_importance'] <= 0.45)
d_signal = d_['signal']
d_rndf_signal_TF = pd.concat([d_signal, d_TF], axis=1)
d_rndf_signal_TF.columns = ['signal','rndf_importance']
d2_TF = (d2_['cumulative_importance'] <= 0.86)
d_gbrf_signal = d2_['signal']
d_gbrf_signal_TF = pd.concat([d_gbrf_signal, d2_TF], axis=1)
d_gbrf_signal_TF.columns = ['signal','gbm_importance']
d3_TF = (abs(d3_['corr']) >= 0.045)
d_corr_signal = d3_['signal']
d_corr_signal_TF = pd.concat([d_corr_signal, d3_TF], axis=1)
d_corr_signal_TF.columns = ['signal','correlation']
d_lasso_signal = d4_['signal']
d_lasso_T = abs(d4_['coef_weights'])>0
d_lasso_signal_TF = pd.concat([d_lasso_signal, d_lasso_T], axis=1)

In [8]:
corr_lasso = pd.merge(d_corr_signal_TF,d_lasso_signal_TF, on='signal')
rndf_gbrt = pd.merge(d_rndf_signal_TF,d_gbrf_signal_TF, on='signal')
feature_selection = pd.merge(corr_lasso,rndf_gbrt,on='signal')
feature_selection['Total'] = np.sum(feature_selection, axis=1)
feature_selection = feature_selection.sort_values(['Total','signal'] , ascending=False)
feature_selection.index = range(1, len(feature_selection)+1)
feature_selection

signal  correlation  coef_weights  rndf_importance  gbm_importance  \
1     signal65         True          True             True            True   
2     signal60         True          True             True            True   
3     signal59         True          True             True            True   
4    signal461         True          True             True            True   
5     signal41         True          True             True            True   
6    signal349         True          True             True            True   
7     signal34         True          True             True            True   
8     signal15         True          True             True            True   
9    signal131         True          True             True            True   
10   signal122         True          True             True            True   
11   signal104         True          True             True            True   
12    signal82        False          True             True            True   
13    signal77         True          True             True           False   
14   signal576         True          True             True           False   
15   signal572        False          True             True            True   
16   signal563         True          True            False            True   
17   signal511         True          True             True           False   
18   signal478         True         False             True            True   
19   signal469         True          True             True           False   
20   signal438         True          True            False            True   
21   signal434         True          True            False            True   
22   signal432         True          True             True           False   
23   signal366         True          True            False            True   
24   signal342         True         False             True            True   
25   signal334         True         False             True            True   
26   signal320         True          True             True           False   
27    signal32         True          True             True           False   
28   signal317         True          True             True           False   
29    signal29         True          True             True           False   
30    signal23         True          True            False            True   
31    signal22         True          True             True           False   
32   signal211         True         False             True            True   
33   signal164         True         False             True            True   
34   signal130         True          True             True           False   
35   signal127         True          True             True           False   
36   signal125         True          True             True           False   
37   signal123         True          True             True           False   
38   signal116        False          True             True            True   
39   signal115         True          True            False            True   
40   signal101         True          True            False            True   
41   signal100         True          True            False            True   
42    signal91         True          True            False           False   
43    signal89        False          True            False            True   
44    signal80         True         False             True           False   
45    signal76        False          True             True           False   
46    signal69         True         False             True           False   
47    signal66         True         False             True           False   
48   signal588        False          True             True           False   
49   signal583         True          True            False           False   
50   signal578         True          True            False           False   
51    signal57         True   

In [9]:
selected_feature = feature_selection[feature_selection['Total']>=3]
#selected_feature.columns = ['signal','Pearson Correlation','Auc Score','Rndf','GBM','Lasso','Total']
selected_feature.columns = ['signal','Pearson Correlation','Rndf','GBM','Lasso','Total']
selected_feature

signal  Pearson Correlation   Rndf    GBM  Lasso  Total
1    signal65                 True   True   True   True      4
2    signal60                 True   True   True   True      4
3    signal59                 True   True   True   True      4
4   signal461                 True   True   True   True      4
5    signal41                 True   True   True   True      4
6   signal349                 True   True   True   True      4
7    signal34                 True   True   True   True      4
8    signal15                 True   True   True   True      4
9   signal131                 True   True   True   True      4
10  signal122                 True   True   True   True      4
11  signal104                 True   True   True   True      4
12   signal82                False   True   True   True      3
13   signal77                 True   True   True  False      3
14  signal576                 True   True   True  False      3
15  signal572                False   True   True   True      3
16  signal563                 True   True  False   True      3
17  signal511                 True   True   True  False      3
18  signal478                 True  False   True   True      3
19  signal469                 True   True   True  False      3
20  signal438                 True   True  False   True      3
21  signal434                 True   True  False   True      3
22  signal432                 True   True   True  False      3
23  signal366                 True   True  False   True      3
24  signal342                 True  False   True   True      3
25  signal334                 True  False   True   True      3
26  signal320                 True   True   True  False      3
27   signal32                 True   True   True  False      3
28  signal317                 True   True   True  False      3
29   signal29                 True   True   True  False      3
30   signal23                 True   True  False   True      3
31   signal22                 True   True   True  False      3
32  signal211                 True  False   True   True      3
33  signal164                 True  False   True   True      3
34  signal130                 True   True   True  False      3
35  signal127                 True   True   True  False      3
36  signal125                 True   True   True  False      3
37  signal123                 True   True   True  False      3
38  signal116                False   True   True   True      3
39  signal115                 True   True  False   True      3
40  signal101                 True   True  False   True      3
41  signal100                 True   True  False   True      3

In [10]:
selected_feature_list = list(selected_feature['signal'])
X_selected_feature = X[selected_feature_list]

In [11]:
from sklearn.preprocessing import StandardScaler
x_std = StandardScaler().fit_transform(X_selected_feature)
X_std = pd.DataFrame(x_std,columns=X_selected_feature.columns)
X_std

signal65   signal60  signal59  signal461  signal41  signal349  \
0     0.236986  -0.493495  1.322946   0.055621 -0.279222  -0.271990   
1    -0.273162  -0.227091  1.043995   0.844120  0.429511  -0.890822   
2    -0.880660   2.193037 -0.070631   0.237211 -2.239938  -1.204476   
3    -0.992326   2.251350 -0.070631  -0.113738  0.373096   1.355622   
4     2.364819  -1.604670  0.566130   0.127132  0.351784  -0.009198   
5    -1.780873   2.663138  0.402526   1.022604 -0.335637  -0.687370   
6    -0.535635  -0.090024  1.043995  -0.413099  0.271132  -0.594122   
7    -1.949077   2.750975  0.402526  -1.519457  0.422824  -0.263513   
8    -1.515823   2.524726  0.402526   0.632605 -0.287162  -1.221431   
9    -1.784155   2.664851  0.402526  -0.528499  0.422824   0.592679   
10   -1.688617   2.614960 -1.300604   0.082477 -2.239938  -0.678893   
11   -1.134173   2.325425  0.402526   0.369374 -0.287162   1.041968   
12   -0.638684   2.066675 -0.070631   0.133112  0.373096  -0.772142   
13    0.129528  -0.437379  0.271878   0.389612  0.423660   1.915114   
14    0.364920   1.542583 -0.010603  -0.374290  0.275729   1.533642   
15   -0.195362   1.835168  0.237745  -0.599867  0.275729   1.711663   
16    1.523942  -1.165556 -0.446096  -0.729269  0.249820  -1.136659   
17    1.003365  -0.893706 -0.446096  -0.607814  0.253581  -0.187219   
18   -0.207987  -0.261126 -0.446096  -0.657181 -2.667518  -0.526304   
19   -0.608663   2.050998 -0.070631  -0.449110  0.373096   1.542120   
20   -0.909956   0.105449 -1.200558  -0.474938 -2.780514   0.177299   
21   -0.134778  -0.299356 -1.200558   0.165123 -2.665011  -0.051584   
22    0.625581  -0.696423 -0.446096   0.717630 -2.590210   0.575725   
23    0.212824   1.622009 -0.010603  -0.247109  0.275729   1.177602   
24    0.824913   1.302370 -0.256598   0.297436 -2.238267   2.160951   
25   -0.713926   0.003081  1.113439  -0.828513  0.349277  -1.034933   
26    1.281784  -1.039099 -0.045914  -1.031106  0.429511  -0.984070   
27    0.415437   1.516202  0.639105   0.092855  0.364321   1.813388   
28    1.275925   1.066847  0.639105  -1.022522  0.363485   2.474606   
29    0.955042   1.234416 -0.557912  -0.340801 -2.249550   2.033794   
30   -2.025588   2.790930  1.113439  -0.315168 -0.089502   2.652626   
31    1.268959   1.070485 -0.557912  -0.788016 -2.244535   1.830343   
32    0.571218  -0.668034  0.300127  -0.970724  0.249820   0.541816   
33   -0.997259   0.151040  1.113439  -0.296671 -0.390798   0.194253   
34    0.383222   1.533025  0.193019   0.332494  0.364321   1.576028   
35    1.927900  -1.376507 -0.070631  -1.018177  0.365992   0.762222   
36    1.101842   1.157755  0.639105  -0.592213 -2.249550   1.855774   
37    1.200320   1.106329 -0.557912  -0.777135 -2.249550   1.618414   
38   -1.097750   2.306404 -0.070631  -0.234788 -2.239938   1.576028   
39   -0.810008   2.156142  1.113439  -0.171052 -0.089502   0.524862   
40    0.865725   1.281058  0.639105   0.116229  0.274475   1.533642   
41    0.425686  -0.592036 -0.045914  -0.866024  0.394408  -1.009502   
42    0.385417  -0.571007  0.300127  -0.618266  0.180451  -0.729756   
43    0.027587   1.718742  0.800355   1.129832  0.480910   2.381357   
44    2.244213   0.561197  0.150647  -1.248174  0.274475  -0.492396   
45    2.903517   0.216902  0.150647  -1.091789  0.480910  -0.992548   
46    1.481116   0.959694 -0.045914  -0.600482 -2.238267  -0.695847   
47   -0.742296   2.120782 -0.010603  -0.454227  0.275729   0.050142   
48   -1.125032   2.320651  0.469616  -0.601878 -0.089502  -0.102447   
49   -0.777249   2.139035  0.150647   0.449927  0.424496  -0.255036   
50   -0.907036   2.206811  0.175364  -0.180206 -0.089502  -1.077319   
51   -0.390486   1.937063  0.300127   0.804133 -2.238267   0.101004   
52    3.596506  -0.144983  0.802709  -0.049506  0.480910  -0.661939   
53   -0.247168  -0.240665  1.113439   0.121144 -0.372968  -0.534782   
54   -0.119778   1.795697  0.150647  -0.267827  0.285340  -0.305899   
55   -0.492447   1.990309 -0.0

In [32]:
from sklearn.model_selection import KFold
kfold = KFold(n_splits = 10,random_state=1,shuffle=True)
idx = []
for train_idx, test_idx in kfold.split(X_std):
    idx.append([train_idx,test_idx])

In [33]:
X_train_1 = X_std.loc[idx[0][0]]
X_test_1 = X_std.loc[idx[0][1]]
y_train_1 = y.loc[idx[0][0]]
y_test_1 = y.loc[idx[0][1]]
X_train_2 = X_std.loc[idx[1][0]]
X_test_2 = X_std.loc[idx[1][1]]
y_train_2 = y.loc[idx[1][0]]
y_test_2 = y.loc[idx[1][1]]
X_train_3 = X_std.loc[idx[2][0]]
X_test_3 = X_std.loc[idx[2][1]]
y_train_3 = y.loc[idx[2][0]]
y_test_3 = y.loc[idx[2][1]]
X_train_4 = X_std.loc[idx[3][0]]
X_test_4 = X_std.loc[idx[3][1]]
y_train_4 = y.loc[idx[3][0]]
y_test_4 = y.loc[idx[3][1]]
X_train_5 = X_std.loc[idx[4][0]]
X_test_5 = X_std.loc[idx[4][1]]
y_train_5 = y.loc[idx[4][0]]
y_test_5 = y.loc[idx[4][1]]
X_train_6 = X_std.loc[idx[5][0]]
X_test_6 = X_std.loc[idx[5][1]]
y_train_6 = y.loc[idx[5][0]]
y_test_6 = y.loc[idx[5][1]]
X_train_7 = X_std.loc[idx[6][0]]
X_test_7 = X_std.loc[idx[6][1]]
y_train_7 = y.loc[idx[6][0]]
y_test_7 = y.loc[idx[6][1]]
X_train_8 = X_std.loc[idx[7][0]]
X_test_8 = X_std.loc[idx[7][1]]
y_train_8 = y.loc[idx[7][0]]
y_test_8 = y.loc[idx[7][1]]
X_train_9 = X_std.loc[idx[8][0]]
X_test_9 = X_std.loc[idx[8][1]]
y_train_9 = y.loc[idx[8][0]]
y_test_9 = y.loc[idx[8][1]]
X_train_10 = X_std.loc[idx[9][0]]
X_test_10 = X_std.loc[idx[9][1]]
y_train_10 = y.loc[idx[9][0]]
y_test_10 = y.loc[idx[9][1]]
a = []
a.append(y_test_1.value_counts())
a.append(y_test_2.value_counts())
a.append(y_test_3.value_counts())
a.append(y_test_4.value_counts())
a.append(y_test_5.value_counts())
a.append(y_test_6.value_counts())
a.append(y_test_7.value_counts())
a.append(y_test_8.value_counts())
a.append(y_test_9.value_counts())
a.append(y_test_10.value_counts())
a = pd.DataFrame(a)
a.index = ['1','2','3','4','5','6','7','8','9','10']
a

-1   1
1   145  12
2   149   8
3   145  12
4   147  10
5   145  12
6   143  14
7   146  11
8   147   9
9   148   8
10  148   8

In [34]:
from sklearn.model_selection import KFold
from sklearn.linear_model import LogisticRegression
from imblearn.over_sampling import ADASYN
from imblearn.over_sampling import SMOTE
from sklearn.metrics import accuracy_score, f1_score, roc_auc_score
lr_accuracy = []
lr_auc = []
lr_f1 = []

for train_idx, test_idx in kfold.split(X_std):
    X_train = X_std.iloc[train_idx]
    X_test = X_std.iloc[test_idx]
    y_train = y.iloc[train_idx]
    y_test = y.iloc[test_idx]
    
    X_train, y_train = SMOTE(random_state=4).fit_resample(X_train, y_train)
    lr = LogisticRegression()
    lr.fit(X_train, y_train)
    lr_predict = lr.predict(X_test)
    lr_accuracy.append(accuracy_score(y_test, lr_predict))
    lr_auc.append(roc_auc_score(y_test,lr_predict))
    lr_f1.append(f1_score(y_test,lr_predict))

In [35]:
lr_dict = {'lr_acc':lr_accuracy,'lr_auc':lr_auc,'lr_f1':lr_f1}
lr_df = pd.DataFrame(lr_dict)
lr_df

lr_acc    lr_auc     lr_f1
0  0.789809  0.656897  0.266667
1  0.751592  0.750839  0.235294
2  0.770701  0.684770  0.280000
3  0.738854  0.767347  0.280702
4  0.707006  0.612069  0.206897
5  0.783439  0.752248  0.370370
6  0.700637  0.628892  0.203390
7  0.698718  0.475057  0.078431
8  0.743590  0.687500  0.200000
9  0.807692  0.780405  0.285714

In [36]:
lr_score = pd.DataFrame(np.array(lr_df.mean()).reshape(-1,1),columns=['LogisticRegression'])
lr_score

LogisticRegression
0            0.749204
1            0.679602
2            0.240746

In [39]:
from sklearn.tree import DecisionTreeClassifier
dt_accuracy = []
dt_auc = []
dt_f1 = []

for train_idx, test_idx in kfold.split(X_std):
    X_train = X_std.iloc[train_idx]
    X_test = X_std.iloc[test_idx]
    y_train = y.iloc[train_idx]
    y_test = y.iloc[test_idx]
    
    X_train, y_train = SMOTE(random_state=4).fit_resample(X_train, y_train)
    dt = DecisionTreeClassifier(random_state=5)
    dt.fit(X_train, y_train)
    dt_predict = dt.predict(X_test)
    dt_accuracy.append(accuracy_score(y_test, dt_predict))
    dt_auc.append(roc_auc_score(y_test,dt_predict))
    dt_f1.append(f1_score(y_test,dt_predict))

In [40]:
dt_dict = {'dt_acc':dt_accuracy,'dt_auc':dt_auc,'dt_f1':dt_f1}
dt_df = pd.DataFrame(dt_dict)
dt_df

dt_acc    dt_auc     dt_f1
0  0.847134  0.535057  0.142857
1  0.815287  0.606963  0.171429
2  0.853503  0.614943  0.258065
3  0.898089  0.759184  0.428571
4  0.815287  0.556034  0.171429
5  0.796178  0.598152  0.238095
6  0.847134  0.539539  0.142857
7  0.794872  0.473923  0.058824
8  0.852564  0.567568  0.148148
9  0.852564  0.685811  0.258065

In [41]:
dt_score = pd.DataFrame(np.array(dt_df.mean()).reshape(-1,1),columns=['DecisionTree'])
dt_score

DecisionTree
0      0.837261
1      0.593717
2      0.201834

In [72]:
rf_accuracy = []
rf_auc = []
rf_f1 = []

for train_idx, test_idx in kfold.split(X_std):
    X_train = X_std.iloc[train_idx]
    X_test = X_std.iloc[test_idx]
    y_train = y.iloc[train_idx]
    y_test = y.iloc[test_idx]
    
    X_train, y_train = SMOTE(random_state=4).fit_resample(X_train, y_train)
    rf = RandomForestClassifier(random_state=6)
    rf.fit(X_train, y_train)
    rf_predict = rf.predict(X_test)
    rf_accuracy.append(accuracy_score(y_test, rf_predict))
    rf_auc.append(roc_auc_score(y_test,rf_predict))
    rf_f1.append(f1_score(y_test,rf_predict))

In [73]:
rf_dict = {'rf_acc':rf_accuracy,'rf_auc':rf_auc,'rf_f1':rf_f1}
rf_df = pd.DataFrame(rf_dict)
rf_df

rf_acc    rf_auc     rf_f1
0  0.923567  0.538218  0.142857
1  0.942675  0.555789  0.181818
2  0.904459  0.604310  0.285714
3  0.917197  0.582993  0.235294
4  0.910828  0.531322  0.125000
5  0.917197  0.600150  0.315789
6  0.891720  0.521482  0.105263
7  0.891026  0.472789  0.000000
8  0.923077  0.486486  0.000000
9  0.942308  0.673986  0.400000

In [74]:
rf_score = pd.DataFrame(np.array(rf_df.mean()).reshape(-1,1),columns=['RandomForest'])
rf_score

RandomForest
0      0.916405
1      0.556753
2      0.179174

In [45]:
from sklearn.ensemble import AdaBoostClassifier
bt_accuracy = []
bt_auc = []
bt_f1 = []

for train_idx, test_idx in kfold.split(X_std):
    X_train = X_std.iloc[train_idx]
    X_test = X_std.iloc[test_idx]
    y_train = y.iloc[train_idx]
    y_test = y.iloc[test_idx]
    
    X_train, y_train = SMOTE(random_state=4).fit_resample(X_train, y_train)
    bt = AdaBoostClassifier(random_state=1)
    bt.fit(X_train, y_train)
    bt_predict = bt.predict(X_test)
    bt_accuracy.append(accuracy_score(y_test, bt_predict))
    bt_auc.append(roc_auc_score(y_test,bt_predict))
    bt_f1.append(f1_score(y_test,bt_predict))

In [46]:
bt_dict = {'bt_acc':bt_accuracy,'bt_auc':bt_auc,'bt_f1':bt_f1}
bt_df = pd.DataFrame(bt_dict)
bt_df

bt_acc    bt_auc     bt_f1
0  0.821656  0.674138  0.300000
1  0.853503  0.745386  0.303030
2  0.847134  0.726149  0.368421
3  0.859873  0.738776  0.352941
4  0.808917  0.705460  0.318182
5  0.828025  0.647852  0.307692
6  0.789809  0.508717  0.108108
7  0.769231  0.460317  0.052632
8  0.833333  0.616554  0.187500
9  0.814103  0.842905  0.325581

In [47]:
bt_score = pd.DataFrame(np.array(bt_df.mean()).reshape(-1,1),columns=['boosting'])
bt_score

boosting
0  0.822558
1  0.666625
2  0.262409

In [75]:
score = pd.concat([lr_score,dt_score,rf_score,bt_score],axis=1)

In [76]:
score.index=['accuracy','auc_score','f1_score']

In [77]:
score

LogisticRegression  DecisionTree  RandomForest  boosting
accuracy             0.749204      0.837261      0.916405  0.822558
auc_score            0.679602      0.593717      0.556753  0.666625
f1_score             0.240746      0.201834      0.179174  0.262409

In [78]:
from sklearn.model_selection import KFold
from sklearn.model_selection import RandomizedSearchCV
from scipy.stats import randint as sp_randint

param_distribs = {"C":[0.000001,0.000002,0.000005,0.00001,0.00002,0.00005,0.0001,0.0002,0.0005,0.001,0.002,0.005,0.01,0.02,0.05,0.1,0.2,0.5,1,2,5,10,20,50]
                 }
lr = LogisticRegression()
lr_search = RandomizedSearchCV(lr, param_distributions=param_distribs, n_iter=10, cv=kfold, scoring='roc_auc')
lr_search.fit(X_std,y)

RandomizedSearchCV(cv=KFold(n_splits=10, random_state=1, shuffle=True),
                   estimator=LogisticRegression(),
                   param_distributions={'C': [1e-06, 2e-06, 5e-06, 1e-05, 2e-05,
                                              5e-05, 0.0001, 0.0002, 0.0005,
                                              0.001, 0.002, 0.005, 0.01, 0.02,
                                              0.05, 0.1, 0.2, 0.5, 1, 2, 5, 10,
                                              20, 50]},
                   scoring='roc_auc')

In [79]:
print('final params', lr_search.best_params_)   # 최적의 파라미터 값 출력
print('best score', lr_search.best_score_)

final params {'C': 0.0002}
best score 0.7819815661114697


In [80]:
from sklearn.model_selection import KFold
from sklearn.linear_model import LogisticRegression
from imblearn.over_sampling import ADASYN
from sklearn.metrics import accuracy_score, f1_score, roc_auc_score
lr_accuracy = []
lr_auc = []
lr_f1 = []

for train_idx, test_idx in kfold.split(X_std):
    X_train = X_std.iloc[train_idx]
    X_test = X_std.iloc[test_idx]
    y_train = y.iloc[train_idx]
    y_test = y.iloc[test_idx]
    
    X_train, y_train = ADASYN(random_state=4).fit_resample(X_train, y_train)
    lr = LogisticRegression(C=0.0002)
    lr.fit(X_train, y_train)
    lr_predict = lr.predict(X_test)
    lr_accuracy.append(accuracy_score(y_test, lr_predict))
    lr_auc.append(roc_auc_score(y_test,lr_predict))
    lr_f1.append(f1_score(y_test,lr_predict))

In [81]:
lr_dict = {'lr_acc':lr_accuracy,'lr_auc':lr_auc,'lr_f1':lr_f1}
lr_df = pd.DataFrame(lr_dict)
lr_df

lr_acc    lr_auc     lr_f1
0  0.757962  0.639655  0.240000
1  0.694268  0.720638  0.200000
2  0.777070  0.726437  0.313725
3  0.802548  0.847959  0.367347
4  0.745223  0.747414  0.310345
5  0.777070  0.684316  0.313725
6  0.713376  0.551681  0.150943
7  0.724359  0.592971  0.156863
8  0.782051  0.766892  0.260870
9  0.782051  0.826014  0.291667

In [82]:
lr_score = pd.DataFrame(np.array(lr_df.mean()).reshape(-1,1),columns=['LogisticRegression'])
lr_score

LogisticRegression
0            0.755598
1            0.710398
2            0.260549

In [83]:
from sklearn.model_selection import KFold
from sklearn.model_selection import RandomizedSearchCV
from scipy.stats import randint as sp_randint

param_distribs = {"criterion": ['gini','entropy'], 
                  "max_depth": sp_randint(1, 100),
                  "max_features": sp_randint(1, 100),
                  "max_leaf_nodes": sp_randint(1, 100),
                  "min_samples_split": sp_randint(1, 100),
                  "min_samples_leaf": sp_randint(1, 100),
                 }
dt = DecisionTreeClassifier(random_state=5)
dt_search = RandomizedSearchCV(dt, param_distributions=param_distribs, n_iter=10, cv=kfold, scoring='f1')
dt_search.fit(X_std,y)

C:\Users\mstar\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py:610: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "C:\Users\mstar\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py", line 593, in _fit_and_score
    estimator.fit(X_train, y_train, **fit_params)
  File "C:\Users\mstar\anaconda3\lib\site-packages\sklearn\tree\_classes.py", line 898, in fit
    super().fit(
  File "C:\Users\mstar\anaconda3\lib\site-packages\sklearn\tree\_classes.py", line 288, in fit
    raise ValueError("max_features must be in (0, n_features]")
ValueError: max_features must be in (0, n_features]

  warnings.warn("Estimator fit failed. The score on this train-test"
C:\Users\mstar\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py:610: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameter

C:\Users\mstar\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py:610: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "C:\Users\mstar\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py", line 593, in _fit_and_score
    estimator.fit(X_train, y_train, **fit_params)
  File "C:\Users\mstar\anaconda3\lib\site-packages\sklearn\tree\_classes.py", line 898, in fit
    super().fit(
  File "C:\Users\mstar\anaconda3\lib\site-packages\sklearn\tree\_classes.py", line 288, in fit
    raise ValueError("max_features must be in (0, n_features]")
ValueError: max_features must be in (0, n_features]

  warnings.warn("Estimator fit failed. The score on this train-test"
C:\Users\mstar\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py:610: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameter

C:\Users\mstar\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py:610: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "C:\Users\mstar\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py", line 593, in _fit_and_score
    estimator.fit(X_train, y_train, **fit_params)
  File "C:\Users\mstar\anaconda3\lib\site-packages\sklearn\tree\_classes.py", line 898, in fit
    super().fit(
  File "C:\Users\mstar\anaconda3\lib\site-packages\sklearn\tree\_classes.py", line 288, in fit
    raise ValueError("max_features must be in (0, n_features]")
ValueError: max_features must be in (0, n_features]

  warnings.warn("Estimator fit failed. The score on this train-test"
C:\Users\mstar\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py:610: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameter

C:\Users\mstar\anaconda3\lib\site-packages\sklearn\model_selection\_search.py:918: UserWarning: One or more of the test scores are non-finite: [       nan        nan 0.18272184        nan        nan 0.
        nan        nan 0.02       0.        ]
  warnings.warn(


RandomizedSearchCV(cv=KFold(n_splits=10, random_state=1, shuffle=True),
                   estimator=DecisionTreeClassifier(random_state=5),
                   param_distributions={'criterion': ['gini', 'entropy'],
                                        'max_depth': <scipy.stats._distn_infrastructure.rv_frozen object at 0x00000278AE58E040>,
                                        'max_features': <scipy.stats._distn_infrastructure.rv_frozen object at 0x00000278AE5B9340>,
                                        'max_leaf_nodes': <scipy.stats._distn_infrastructure.rv_frozen object at 0x00000278AE5B99A0>,
                                        'min_samples_leaf': <scipy.stats._distn_infrastructure.rv_frozen object at 0x00000278AE25CE20>,
                                        'min_samples_split': <scipy.stats._distn_infrastructure.rv_frozen object at 0x00000278AE5B92E0>},
                   scoring='f1')

In [84]:
print('final params', dt_search.best_params_)   # 최적의 파라미터 값 출력
print('best score', dt_search.best_score_)

final params {'criterion': 'entropy', 'max_depth': 70, 'max_features': 19, 'max_leaf_nodes': 60, 'min_samples_leaf': 3, 'min_samples_split': 47}
best score 0.18272184471874875


In [85]:
from sklearn.tree import DecisionTreeClassifier
dt_accuracy = []
dt_auc = []
dt_f1 = []

for train_idx, test_idx in kfold.split(X_std):
    X_train = X_std.iloc[train_idx]
    X_test = X_std.iloc[test_idx]
    y_train = y.iloc[train_idx]
    y_test = y.iloc[test_idx]
    
    X_train, y_train = ADASYN(random_state=4).fit_resample(X_train, y_train)
    dt = dt_search.best_estimator_
    dt.fit(X_train, y_train)
    dt_predict = dt.predict(X_test)
    dt_accuracy.append(accuracy_score(y_test, dt_predict))
    dt_auc.append(roc_auc_score(y_test,dt_predict))
    dt_f1.append(f1_score(y_test,dt_predict))

In [86]:
dt_dict = {'dt_acc':dt_accuracy,'dt_auc':dt_auc,'dt_f1':dt_f1}
dt_df = pd.DataFrame(dt_dict)
dt_df

dt_acc    dt_auc     dt_f1
0  0.821656  0.559483  0.176471
1  0.815287  0.488674  0.064516
2  0.828025  0.639368  0.270270
3  0.859873  0.692177  0.312500
4  0.802548  0.702011  0.311111
5  0.770701  0.680819  0.307692
6  0.796178  0.470112  0.058824
7  0.801282  0.477324  0.060606
8  0.891026  0.646959  0.260870
9  0.833333  0.675676  0.235294

In [87]:
dt_score = pd.DataFrame(np.array(dt_df.mean()).reshape(-1,1),columns=['DecisionTree'])
dt_score

DecisionTree
0      0.821991
1      0.603260
2      0.205815

In [88]:
print(rf.get_params())

{'bootstrap': True, 'ccp_alpha': 0.0, 'class_weight': None, 'criterion': 'gini', 'max_depth': None, 'max_features': 'auto', 'max_leaf_nodes': None, 'max_samples': None, 'min_impurity_decrease': 0.0, 'min_impurity_split': None, 'min_samples_leaf': 1, 'min_samples_split': 2, 'min_weight_fraction_leaf': 0.0, 'n_estimators': 100, 'n_jobs': None, 'oob_score': False, 'random_state': 6, 'verbose': 0, 'warm_start': False}


In [89]:
from sklearn.model_selection import KFold
from sklearn.model_selection import RandomizedSearchCV
from scipy.stats import randint as sp_randint

param_distribs = {"n_estimators": sp_randint (1, 500), 
                  "max_depth": sp_randint(1, 100),
                  "max_features": sp_randint(1, 100),
                  "min_samples_split": sp_randint(1, 100),
                  "min_samples_leaf": sp_randint(1, 100),
                 }
forest_reg = RandomForestClassifier(random_state=3)
rnd_search = RandomizedSearchCV(forest_reg, param_distributions=param_distribs, n_iter=10, cv=kfold, scoring='roc_auc')
rnd_search.fit(X_std,y)

C:\Users\mstar\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py:610: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "C:\Users\mstar\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py", line 593, in _fit_and_score
    estimator.fit(X_train, y_train, **fit_params)
  File "C:\Users\mstar\anaconda3\lib\site-packages\sklearn\ensemble\_forest.py", line 387, in fit
    trees = Parallel(n_jobs=self.n_jobs, verbose=self.verbose,
  File "C:\Users\mstar\anaconda3\lib\site-packages\joblib\parallel.py", line 1041, in __call__
    if self.dispatch_one_batch(iterator):
  File "C:\Users\mstar\anaconda3\lib\site-packages\joblib\parallel.py", line 859, in dispatch_one_batch
    self._dispatch(tasks)
  File "C:\Users\mstar\anaconda3\lib\site-packages\joblib\parallel.py", line 777, in _dispatch
    job = self._backend.apply_async(batch, callback=cb)

C:\Users\mstar\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py:610: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "C:\Users\mstar\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py", line 593, in _fit_and_score
    estimator.fit(X_train, y_train, **fit_params)
  File "C:\Users\mstar\anaconda3\lib\site-packages\sklearn\ensemble\_forest.py", line 387, in fit
    trees = Parallel(n_jobs=self.n_jobs, verbose=self.verbose,
  File "C:\Users\mstar\anaconda3\lib\site-packages\joblib\parallel.py", line 1041, in __call__
    if self.dispatch_one_batch(iterator):
  File "C:\Users\mstar\anaconda3\lib\site-packages\joblib\parallel.py", line 859, in dispatch_one_batch
    self._dispatch(tasks)
  File "C:\Users\mstar\anaconda3\lib\site-packages\joblib\parallel.py", line 777, in _dispatch
    job = self._backend.apply_async(batch, callback=cb)

C:\Users\mstar\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py:610: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "C:\Users\mstar\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py", line 593, in _fit_and_score
    estimator.fit(X_train, y_train, **fit_params)
  File "C:\Users\mstar\anaconda3\lib\site-packages\sklearn\ensemble\_forest.py", line 387, in fit
    trees = Parallel(n_jobs=self.n_jobs, verbose=self.verbose,
  File "C:\Users\mstar\anaconda3\lib\site-packages\joblib\parallel.py", line 1041, in __call__
    if self.dispatch_one_batch(iterator):
  File "C:\Users\mstar\anaconda3\lib\site-packages\joblib\parallel.py", line 859, in dispatch_one_batch
    self._dispatch(tasks)
  File "C:\Users\mstar\anaconda3\lib\site-packages\joblib\parallel.py", line 777, in _dispatch
    job = self._backend.apply_async(batch, callback=cb)

C:\Users\mstar\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py:610: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "C:\Users\mstar\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py", line 593, in _fit_and_score
    estimator.fit(X_train, y_train, **fit_params)
  File "C:\Users\mstar\anaconda3\lib\site-packages\sklearn\ensemble\_forest.py", line 387, in fit
    trees = Parallel(n_jobs=self.n_jobs, verbose=self.verbose,
  File "C:\Users\mstar\anaconda3\lib\site-packages\joblib\parallel.py", line 1041, in __call__
    if self.dispatch_one_batch(iterator):
  File "C:\Users\mstar\anaconda3\lib\site-packages\joblib\parallel.py", line 859, in dispatch_one_batch
    self._dispatch(tasks)
  File "C:\Users\mstar\anaconda3\lib\site-packages\joblib\parallel.py", line 777, in _dispatch
    job = self._backend.apply_async(batch, callback=cb)

C:\Users\mstar\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py:610: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "C:\Users\mstar\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py", line 593, in _fit_and_score
    estimator.fit(X_train, y_train, **fit_params)
  File "C:\Users\mstar\anaconda3\lib\site-packages\sklearn\ensemble\_forest.py", line 387, in fit
    trees = Parallel(n_jobs=self.n_jobs, verbose=self.verbose,
  File "C:\Users\mstar\anaconda3\lib\site-packages\joblib\parallel.py", line 1041, in __call__
    if self.dispatch_one_batch(iterator):
  File "C:\Users\mstar\anaconda3\lib\site-packages\joblib\parallel.py", line 859, in dispatch_one_batch
    self._dispatch(tasks)
  File "C:\Users\mstar\anaconda3\lib\site-packages\joblib\parallel.py", line 777, in _dispatch
    job = self._backend.apply_async(batch, callback=cb)

...

C:\Users\mstar\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py:610: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "C:\Users\mstar\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py", line 593, in _fit_and_score
    estimator.fit(X_train, y_train, **fit_params)
  File "C:\Users\mstar\anaconda3\lib\site-packages\sklearn\ensemble\_forest.py", line 387, in fit
    trees = Parallel(n_jobs=self.n_jobs, verbose=self.verbose,
  File "C:\Users\mstar\anaconda3\lib\site-packages\joblib\parallel.py", line 1041, in __call__
    if self.dispatch_one_batch(iterator):
  File "C:\Users\mstar\anaconda3\lib\site-packages\joblib\parallel.py", line 859, in dispatch_one_batch
    self._dispatch(tasks)
  File "C:\Users\mstar\anaconda3\lib\site-packages\joblib\parallel.py", line 777, in _dispatch
    job = self._backend.apply_async(batch, callback=cb)

C:\Users\mstar\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py:610: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "C:\Users\mstar\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py", line 593, in _fit_and_score
    estimator.fit(X_train, y_train, **fit_params)
  File "C:\Users\mstar\anaconda3\lib\site-packages\sklearn\ensemble\_forest.py", line 387, in fit
    trees = Parallel(n_jobs=self.n_jobs, verbose=self.verbose,
  File "C:\Users\mstar\anaconda3\lib\site-packages\joblib\parallel.py", line 1041, in __call__
    if self.dispatch_one_batch(iterator):
  File "C:\Users\mstar\anaconda3\lib\site-packages\joblib\parallel.py", line 859, in dispatch_one_batch
    self._dispatch(tasks)
  File "C:\Users\mstar\anaconda3\lib\site-packages\joblib\parallel.py", line 777, in _dispatch
    job = self._backend.apply_async(batch, callback=cb)

C:\Users\mstar\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py:610: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "C:\Users\mstar\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py", line 593, in _fit_and_score
    estimator.fit(X_train, y_train, **fit_params)
  File "C:\Users\mstar\anaconda3\lib\site-packages\sklearn\ensemble\_forest.py", line 387, in fit
    trees = Parallel(n_jobs=self.n_jobs, verbose=self.verbose,
  File "C:\Users\mstar\anaconda3\lib\site-packages\joblib\parallel.py", line 1041, in __call__
    if self.dispatch_one_batch(iterator):
  File "C:\Users\mstar\anaconda3\lib\site-packages\joblib\parallel.py", line 859, in dispatch_one_batch
    self._dispatch(tasks)
  File "C:\Users\mstar\anaconda3\lib\site-packages\joblib\parallel.py", line 777, in _dispatch
    job = self._backend.apply_async(batch, callback=cb)

C:\Users\mstar\anaconda3\lib\site-packages\sklearn\model_selection\_search.py:918: UserWarning: One or more of the test scores are non-finite: [0.7624873  0.75087583        nan        nan        nan        nan
        nan 0.75625241        nan 0.74270968]
  warnings.warn(


RandomizedSearchCV(cv=KFold(n_splits=10, random_state=1, shuffle=True),
                   estimator=RandomForestClassifier(random_state=3),
                   param_distributions={'max_depth': <scipy.stats._distn_infrastructure.rv_frozen object at 0x00000278AE0AEB20>,
                                        'max_features': <scipy.stats._distn_infrastructure.rv_frozen object at 0x00000278AE25CA30>,
                                        'min_samples_leaf': <scipy.stats._distn_infrastructure.rv_frozen object at 0x00000278AE590520>,
                                        'min_samples_split': <scipy.stats._distn_infrastructure.rv_frozen object at 0x00000278AE0AEFD0>,
                                        'n_estimators': <scipy.stats._distn_infrastructure.rv_frozen object at 0x00000278AE25C0D0>},
                   scoring='roc_auc')

In [90]:
print('final params', rnd_search.best_params_)   # 최적의 파라미터 값 출력
print('best score', rnd_search.best_score_)

final params {'max_depth': 30, 'max_features': 6, 'min_samples_leaf': 72, 'min_samples_split': 34, 'n_estimators': 367}
best score 0.7624873046574095


In [91]:
rf_accuracy = []
rf_auc = []
rf_f1 = []

for train_idx, test_idx in kfold.split(X_std):
    X_train = X_std.iloc[train_idx]
    X_test = X_std.iloc[test_idx]
    y_train = y.iloc[train_idx]
    y_test = y.iloc[test_idx]
    
    X_train, y_train = ADASYN(random_state=4).fit_resample(X_train, y_train)
    rf = rnd_search.best_estimator_
    rf.fit(X_train, y_train)
    rf_predict = rf.predict(X_test)
    rf_accuracy.append(accuracy_score(y_test, rf_predict))
    rf_auc.append(roc_auc_score(y_test,rf_predict))
    rf_f1.append(f1_score(y_test,rf_predict))

In [92]:
rf_dict = {'rf_acc':rf_accuracy,'rf_auc':rf_auc,'rf_f1':rf_f1}
rf_df = pd.DataFrame(rf_dict)
rf_df

rf_acc    rf_auc     rf_f1
0  0.853503  0.614943  0.258065
1  0.866242  0.811242  0.363636
2  0.853503  0.729598  0.378378
3  0.878981  0.748980  0.387097
4  0.853503  0.767816  0.410256
5  0.821656  0.644356  0.300000
6  0.796178  0.512142  0.111111
7  0.769231  0.460317  0.052632
8  0.807692  0.662162  0.210526
9  0.839744  0.738176  0.285714

In [93]:
rf_score = pd.DataFrame(np.array(rf_df.mean()).reshape(-1,1),columns=['RandomForest'])
rf_score

RandomForest
0      0.834023
1      0.668973
2      0.275742

In [101]:
from sklearn.model_selection import KFold
from sklearn.model_selection import RandomizedSearchCV
from scipy.stats import randint as sp_randint

param_distribs = {"learning_rate":np.arange(0.05,1,0.05),
                  "n_estimators":sp_randint(1,500)
                 }
bt = AdaBoostClassifier(random_state=1)
bt_search = RandomizedSearchCV(bt, param_distributions=param_distribs, n_iter=10, cv=kfold, scoring='roc_auc')
bt_search.fit(X_std,y)

RandomizedSearchCV(cv=KFold(n_splits=10, random_state=1, shuffle=True),
                   estimator=AdaBoostClassifier(random_state=1),
                   param_distributions={'learning_rate': array([0.05, 0.1 , 0.15, 0.2 , 0.25, 0.3 , 0.35, 0.4 , 0.45, 0.5 , 0.55,
       0.6 , 0.65, 0.7 , 0.75, 0.8 , 0.85, 0.9 , 0.95]),
                                        'n_estimators': <scipy.stats._distn_infrastructure.rv_frozen object at 0x00000278AE315250>},
                   scoring='roc_auc')

In [102]:
print('final params', bt_search.best_params_)   # 최적의 파라미터 값 출력
print('best score', bt_search.best_score_)

final params {'learning_rate': 0.8500000000000001, 'n_estimators': 48}
best score 0.7453543214617475


In [103]:
from sklearn.ensemble import AdaBoostClassifier
bt_accuracy = []
bt_auc = []
bt_f1 = []

for train_idx, test_idx in kfold.split(X_std):
    X_train = X_std.iloc[train_idx]
    X_test = X_std.iloc[test_idx]
    y_train = y.iloc[train_idx]
    y_test = y.iloc[test_idx]
    
    X_train, y_train = ADASYN(random_state=4).fit_resample(X_train, y_train)
    bt = bt_search.best_estimator_
    bt.fit(X_train, y_train)
    bt_predict = bt.predict(X_test)
    bt_accuracy.append(accuracy_score(y_test, bt_predict))
    bt_auc.append(roc_auc_score(y_test,bt_predict))
    bt_f1.append(f1_score(y_test,bt_predict))

In [104]:
bt_dict = {'bt_acc':bt_accuracy,'bt_auc':bt_auc,'bt_f1':bt_f1}
bt_df = pd.DataFrame(bt_dict)
bt_df

bt_acc    bt_auc     bt_f1
0  0.808917  0.590805  0.210526
1  0.847134  0.682886  0.250000
2  0.853503  0.653161  0.303030
3  0.821656  0.718367  0.300000
4  0.751592  0.597989  0.204082
5  0.853503  0.694056  0.378378
6  0.789809  0.508717  0.108108
7  0.807692  0.480726  0.062500
8  0.858974  0.570946  0.153846
9  0.826923  0.731419  0.270270

In [105]:
bt_score = pd.DataFrame(np.array(bt_df.mean()).reshape(-1,1),columns=['boosting'])
bt_score

boosting
0  0.821970
1  0.622907
2  0.224074

In [106]:
score = pd.concat([lr_score,dt_score,rf_score,bt_score],axis=1)
score.index=['accuracy','auc_score','f1_score']
score

LogisticRegression  DecisionTree  RandomForest  boosting
accuracy             0.755598      0.821991      0.834023  0.821970
auc_score            0.710398      0.603260      0.668973  0.622907
f1_score             0.260549      0.205815      0.275742  0.224074